
# <font color='purple'> Telecom Project </font> 

<div style="border:solid black 2px; padding: 20px">
<div class="alert alert-block alert-info">
    
- <h3> Project Description</h3> 
    Our client is a virtual telephony sevice CallMeMaybe. They want to develop new functions that will give supervisors information on the clients with non-optimal plans.
    
- <h3>Project Goal</h3>

    - Find clients who overpay for their current plan.
    - Calculate the possible loss in profits from clients who switch the plan.
    - Provide a possible way to measure the increase in loyalty after the campaign.
    
</div>
</div>

#### Presentation and Dashboard
* Dashboard :    https://public.tableau.com/profile/yevgeniya.gimelfarb#!/vizhome/TelecomProject_16100278001630/Dashboard1?publish=yes
* Presentation: https://drive.google.com/file/d/10M0bly7zgquL8IaIipKgLqEALTVbCm3L/view?usp=sharing


## <font color='purple'>Table of contents</font>

* [Step 1. Open the data file and read the general information](#step1)

* [Step 2. Data Preprocessing](#step2)
    
   * [Step 2a.Missng values](#step2a)
   
   * [Step 2b.Duplicates](#step2b)
   
   * [Step 2c.Other anomalies/outliers](#step2c)
    
* [Step 3.Exploratory Data Analysis (EDA)](#step3)

* [Step 4.Business metrics analysis](#step4)

* [Step 5. Hypothesis testing](#step5)

* [Step 6. Final conclusions and recommendations](#step6)

### Step 1. Open the data file and read the general information<a name="step1"></a>

In [55]:
## importing the libraries
import seaborn as sns
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from scipy import stats as st
from functools import reduce
import math
import datetime as dt
!pip install -q plotly==4.9.0 --no-warn-script-location
!pip install -q usaddress --no-warn-script-location
import usaddress 
!pip install -q seaborn --upgrade --no-warn-script-location
import plotly.express as px
from scipy.stats import mannwhitneyu
from scipy.stats import norm
import plotly.graph_objects as go 
from sklearn.preprocessing import StandardScaler
from scipy import stats
import warnings
warnings.filterwarnings('ignore')
%matplotlib inline
from scipy.stats.stats import pearsonr
import statsmodels.api as sm
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
!pip install -q squarify --no-warn-script-location
import squarify
import os
from plotly.subplots import make_subplots

In [56]:
## opening the data
path = '/datasets/'
# path = '/Users/yevgeniyagimelfarb/'
telecom = pd.read_csv(os.path.join(path,'telecom_dataset_us.csv'))
clients = pd.read_csv(os.path.join(path,'telecom_clients_us.csv'),
                               parse_dates = ['date_start'])

In [57]:
#general info
telecom.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 53902 entries, 0 to 53901
Data columns (total 9 columns):
user_id                53902 non-null int64
date                   53902 non-null object
direction              53902 non-null object
internal               53785 non-null object
operator_id            45730 non-null float64
is_missed_call         53902 non-null bool
calls_count            53902 non-null int64
call_duration          53902 non-null int64
total_call_duration    53902 non-null int64
dtypes: bool(1), float64(1), int64(4), object(3)
memory usage: 3.3+ MB


In [58]:
telecom.head()

user_id                       date direction internal  operator_id  \
0   166377  2019-08-04 00:00:00+03:00        in    False          NaN   
1   166377  2019-08-05 00:00:00+03:00       out     True     880022.0   
2   166377  2019-08-05 00:00:00+03:00       out     True     880020.0   
3   166377  2019-08-05 00:00:00+03:00       out     True     880020.0   
4   166377  2019-08-05 00:00:00+03:00       out    False     880022.0   

   is_missed_call  calls_count  call_duration  total_call_duration  
0            True            2              0                    4  
1            True            3              0                    5  
2            True            1              0                    1  
3           False            1             10                   18  
4            True            3              0                   25

In [59]:
#checking the dates (timezones)
telecom['date'].unique()

array(['2019-08-04 00:00:00+03:00', '2019-08-05 00:00:00+03:00',
       '2019-08-06 00:00:00+03:00', '2019-08-07 00:00:00+03:00',
       '2019-08-08 00:00:00+03:00', '2019-08-09 00:00:00+03:00',
       '2019-08-12 00:00:00+03:00', '2019-08-13 00:00:00+03:00',
       '2019-08-14 00:00:00+03:00', '2019-08-15 00:00:00+03:00',
       '2019-08-16 00:00:00+03:00', '2019-08-19 00:00:00+03:00',
       '2019-08-20 00:00:00+03:00', '2019-08-21 00:00:00+03:00',
       '2019-08-22 00:00:00+03:00', '2019-08-23 00:00:00+03:00',
       '2019-08-24 00:00:00+03:00', '2019-08-26 00:00:00+03:00',
       '2019-08-27 00:00:00+03:00', '2019-08-28 00:00:00+03:00',
       '2019-08-29 00:00:00+03:00', '2019-08-30 00:00:00+03:00',
       '2019-09-02 00:00:00+03:00', '2019-09-03 00:00:00+03:00',
       '2019-09-04 00:00:00+03:00', '2019-09-05 00:00:00+03:00',
       '2019-09-06 00:00:00+03:00', '2019-09-09 00:00:00+03:00',
       '2019-09-10 00:00:00+03:00', '2019-09-11 00:00:00+03:00',
       '2019-09-12 00:00:

* There is only 1 timezone, therefore we can get rid of it and continue our analysis with clean date column.

In [60]:
#getting rif of timezone 
telecom['date'] =pd.to_datetime(telecom['date']). dt. tz_localize(None)

In [61]:
 telecom.head()

user_id       date direction internal  operator_id  is_missed_call  \
0   166377 2019-08-04        in    False          NaN            True   
1   166377 2019-08-05       out     True     880022.0            True   
2   166377 2019-08-05       out     True     880020.0            True   
3   166377 2019-08-05       out     True     880020.0           False   
4   166377 2019-08-05       out    False     880022.0            True   

   calls_count  call_duration  total_call_duration  
0            2              0                    4  
1            3              0                    5  
2            1              0                    1  
3            1             10                   18  
4            3              0                   25

* There are 53902 rows and 9 columns in telecom dataset.
* We have got NaN values in operator_id column( which could be explained by the fact that not every call is made through operator).
* We will look for anomalies and duplicates on the next stage of our analysis.

In [62]:
#general info
clients.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 732 entries, 0 to 731
Data columns (total 3 columns):
user_id        732 non-null int64
tariff_plan    732 non-null object
date_start     732 non-null datetime64[ns]
dtypes: datetime64[ns](1), int64(1), object(1)
memory usage: 17.3+ KB


* In clients dataset threre are 3 columns and 732 rows.
* There are no obvious missing values.
* The data types seem correct.


### Step 2.  Data Preproseccing<a name="step2"></a>

#### Step 2a. Missng values<a name="step2a"></a>

In [63]:
telecom.nunique()

user_id                 307
date                    119
direction                 2
internal                  2
operator_id            1092
is_missed_call            2
calls_count             502
call_duration          5373
total_call_duration    6040
dtype: int64

In [64]:
clients.nunique()

user_id        732
tariff_plan      3
date_start      73
dtype: int64

* There are only 307 unique users in telecom dataset.
* We do not see any missing values that could affect our analysis.



#### Step 2b. Duplicates<a name="step2b"></a>

In [65]:

# looking for duplicates
data = [telecom,clients]

for i in data:
    print(i.duplicated().sum())

4900
0


* There are 4900 duplicates in telecom dataset, which is 9% of the data. Seems like a technical problem.
* We will check how there duplicates are allocated and distributed.


In [66]:
#how do they look like
telecom[telecom.duplicated()]

user_id       date direction internal  operator_id  is_missed_call  \
8       166377 2019-08-05       out    False     880020.0            True   
28      166377 2019-08-12        in    False          NaN            True   
44      166377 2019-08-14       out    False     880026.0           False   
45      166377 2019-08-14        in    False          NaN            True   
51      166377 2019-08-15       out    False     880026.0           False   
...        ...        ...       ...      ...          ...             ...   
53869   168601 2019-11-25        in    False     952914.0           False   
53874   168601 2019-11-26        in    False     952914.0           False   
53875   168601 2019-11-26        in    False          NaN            True   
53885   168603 2019-11-20       out    False     959118.0            True   
53900   168606 2019-11-15       out     True     957922.0           False   

       calls_count  call_duration  total_call_duration  
8                8              0                   50  
28               2              0                   34  
44              10           1567                 1654  
45               1              0                    3  
51              11           1413                 1473  
...            ...            ...                  ...  
53869            7           1229                 1282  
53874            4            539                  562  
53875            3              0                   35  
53885            3              0                   89  
53900            4           3130                 3190  

[4900 rows x 9 columns]

In [67]:
#amount of duplicates in each column
for i in telecom[telecom.duplicated()].columns:
    print(i,":",telecom[telecom.duplicated()][i].nunique())

user_id : 269
date : 115
direction : 2
internal : 2
operator_id : 776
is_missed_call : 2
calls_count : 178
call_duration : 1547
total_call_duration : 1820


In [68]:
#distribution of duplicates by date
telecom[telecom.duplicated()]['date'].dt.date.unique()

array([datetime.date(2019, 8, 5), datetime.date(2019, 8, 12),
       datetime.date(2019, 8, 14), datetime.date(2019, 8, 15),
       datetime.date(2019, 8, 19), datetime.date(2019, 8, 22),
       datetime.date(2019, 8, 23), datetime.date(2019, 8, 27),
       datetime.date(2019, 8, 29), datetime.date(2019, 9, 3),
       datetime.date(2019, 9, 5), datetime.date(2019, 9, 10),
       datetime.date(2019, 9, 11), datetime.date(2019, 9, 12),
       datetime.date(2019, 9, 16), datetime.date(2019, 9, 23),
       datetime.date(2019, 9, 25), datetime.date(2019, 9, 26),
       datetime.date(2019, 9, 27), datetime.date(2019, 10, 3),
       datetime.date(2019, 10, 4), datetime.date(2019, 10, 8),
       datetime.date(2019, 10, 10), datetime.date(2019, 10, 11),
       datetime.date(2019, 10, 14), datetime.date(2019, 10, 18),
       datetime.date(2019, 10, 22), datetime.date(2019, 10, 23),
       datetime.date(2019, 10, 28), datetime.date(2019, 10, 29),
       datetime.date(2019, 10, 31), datetime.date(

* There are duplicates created during the whole period.
* We have duplicates in every column.
* Therefore, we will drop them in order to not affect the current analysis and we will also inform the team that there has been a tech problem of double registration of calls.

In [69]:
#dropping the duplicates
telecom = telecom.drop_duplicates()

* In order to achive our goal we will merge the two datasets leaving only those users,we have tariff plan information about.

In [70]:
#merging the datasets
telecom_merged = telecom.merge(clients,how='inner')

In [71]:
telecom_merged.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 49002 entries, 0 to 49001
Data columns (total 11 columns):
user_id                49002 non-null int64
date                   49002 non-null datetime64[ns]
direction              49002 non-null object
internal               48892 non-null object
operator_id            41546 non-null float64
is_missed_call         49002 non-null bool
calls_count            49002 non-null int64
call_duration          49002 non-null int64
total_call_duration    49002 non-null int64
tariff_plan            49002 non-null object
date_start             49002 non-null datetime64[ns]
dtypes: bool(1), datetime64[ns](2), float64(1), int64(4), object(3)
memory usage: 4.2+ MB


In [72]:
#missing values in internal
telecom_merged.isna().sum()


user_id                   0
date                      0
direction                 0
internal                110
operator_id            7456
is_missed_call            0
calls_count               0
call_duration             0
total_call_duration       0
tariff_plan               0
date_start                0
dtype: int64

* We are going to assume that missing values in internal calls are for calls that have not been assigned a direction by mistake.
* We shall drop these calls for now as they are of no use to our analysis.

In [73]:
telecom_merged = telecom_merged[telecom_merged['internal'].notna()]

In [74]:
telecom_merged.head(10)

user_id       date direction internal  operator_id  is_missed_call  \
0   166377 2019-08-04        in    False          NaN            True   
1   166377 2019-08-05       out     True     880022.0            True   
2   166377 2019-08-05       out     True     880020.0            True   
3   166377 2019-08-05       out     True     880020.0           False   
4   166377 2019-08-05       out    False     880022.0            True   
5   166377 2019-08-05       out    False     880020.0           False   
6   166377 2019-08-05       out    False     880020.0            True   
7   166377 2019-08-05        in    False          NaN            True   
8   166377 2019-08-06        in    False          NaN            True   
9   166377 2019-08-06       out    False     881278.0            True   

   calls_count  call_duration  total_call_duration tariff_plan date_start  
0            2              0                    4           B 2019-08-01  
1            3              0                    5           B 2019-08-01  
2            1              0                    1           B 2019-08-01  
3            1             10                   18           B 2019-08-01  
4            3              0                   25           B 2019-08-01  
5            2              3                   29           B 2019-08-01  
6            8              0                   50           B 2019-08-01  
7            6              0                   35           B 2019-08-01  
8            4              0                   62           B 2019-08-01  
9            3              0                   29           B 2019-08-01

#### Step 2c. Other anomalies / outliers <a name="step2c"></a>

* We will check the data for anomalies: missing calls with positive duration( not total durationg, as it includes waiting).


In [75]:
##outliers 
outliers = telecom_merged.query('is_missed_call==True & call_duration >0')
outliers

user_id       date direction internal  operator_id  is_missed_call  \
1471    166405 2019-11-19        in    False     939478.0            True   
1498    166405 2019-11-21        in    False     882686.0            True   
1518    166405 2019-11-22        in    False     882686.0            True   
2089    166407 2019-09-23        in    False     888534.0            True   
2625    166482 2019-11-05        in    False     934074.0            True   
...        ...        ...       ...      ...          ...             ...   
46924   168336 2019-11-01        in    False     947304.0            True   
46981   168336 2019-11-12        in    False     947304.0            True   
47007   168336 2019-11-15        in    False     947304.0            True   
47149   168336 2019-11-27        in    False     958416.0            True   
48383   168412 2019-11-05        in    False     953464.0            True   

       calls_count  call_duration  total_call_duration tariff_plan date_start  
1471             1            165                  173           B 2019-08-02  
1498             1              1                    5           B 2019-08-02  
1518             1              1                    5           B 2019-08-02  
2089             1            133                  156           A 2019-08-02  
2625             1              1                   15           C 2019-08-05  
...            ...            ...                  ...         ...        ...  
46924            1              1                   20           C 2019-10-22  
46981            1             69                   72           C 2019-10-22  
47007            1             46                   49           C 2019-10-22  
47149            1             40                   65           C 2019-10-22  
48383            1              1                    7           C 2019-10-24  

[295 rows x 11 columns]

* There are 296 rows with such values.
* We are going to drop them before we aggregate our data.

In [76]:
#list of rows with anomalies
list_of_rows = outliers.index.tolist()
list_of_rows

[1471,
 1498,
 1518,
 2089,
 2625,
 2708,
 3093,
 3632,
 3717,
 3724,
 3811,
 4560,
 5443,
 5565,
 5592,
 5601,
 5717,
 5803,
 5896,
 5986,
 6040,
 6086,
 6137,
 6191,
 6206,
 6209,
 6317,
 6329,
 6380,
 6431,
 6448,
 6495,
 6564,
 6880,
 6953,
 7642,
 8893,
 9173,
 9565,
 10615,
 11259,
 11451,
 11515,
 11521,
 11746,
 11821,
 11989,
 12198,
 13117,
 13126,
 13144,
 13151,
 13801,
 14657,
 14707,
 14719,
 14742,
 14775,
 14812,
 14825,
 14866,
 14907,
 14929,
 14955,
 14956,
 14967,
 14980,
 15005,
 15046,
 15119,
 15140,
 15186,
 15209,
 15254,
 15267,
 15287,
 15299,
 15307,
 15431,
 15438,
 15443,
 15531,
 15570,
 15583,
 15593,
 15604,
 15632,
 15662,
 15666,
 15693,
 15767,
 15900,
 16117,
 16561,
 16565,
 16761,
 17489,
 17568,
 18069,
 18249,
 18301,
 18317,
 19857,
 20164,
 20622,
 20634,
 20651,
 20665,
 20691,
 20705,
 20729,
 20744,
 20749,
 20784,
 20803,
 20811,
 20832,
 20851,
 20856,
 20861,
 20878,
 20902,
 20917,
 23332,
 23420,
 23696,
 24091,
 24186,
 24282,
 24340,

In [77]:
#dropping the anomalies
telecom_merged = telecom_merged.drop(telecom_merged.index[list_of_rows])



In [78]:
#checking the dates (min and max)
telecom_merged['date'].min()

Timestamp('2019-08-02 00:00:00')

In [79]:
telecom_merged['date'].max()

Timestamp('2019-11-28 00:00:00')

* All the data was collected during one year therefore we can create a month column without risking messing up the data.

In [80]:
#month
telecom_merged['event_month'] = pd.DatetimeIndex(telecom_merged['date']).month
telecom_merged['event_month']

0         8
1         8
2         8
3         8
4         8
         ..
48997    11
48998    11
48999    11
49000    11
49001    11
Name: event_month, Length: 48597, dtype: int64

* Now the data is ready for aggregation.
* We will check the distribution of some values on the next stage and then continue to our final goal.

### Step 3. Exploratory Data Analysis <a name="step3"></a>


* We will check the share of internal/external calls in the data.
* Then check the call duration by plans.

In [81]:
#A column for duration in minutes
telecom_merged['duration_in_minutes'] = telecom_merged['call_duration'] / 60


In [82]:
#histogram of call duration by plans
fig = px.histogram(telecom_merged,y='duration_in_minutes',x='event_month',color='tariff_plan',
                  labels={'duration_in_minutes':'Calls Duration in Minutes','event_month':'Month','tariff_plan':'Plan'})
fig.update_layout(title_text='Calls Duration by Plans')
fig.show()

In [83]:
#internal/external calls
fig = px.histogram(telecom_merged,y='duration_in_minutes',x='internal',color='tariff_plan',
                   labels={'duration_in_minutes':'Calls Duration in Minutes','internal':'Iternal','tariff_plan':'Plan'})
fig.update_layout(title_text='Internal/External Calls by Plans')
fig.show()

* We see that external calls prevail for all of the plans.
* This sounds dangerous as having so many external calls clients may realise it is better for them to switch company.
* We can see that calls duration is the highest for A plan(as we were expecting), but the second place is taken by users with plan C. 
* Perhaps these exact users are overpaying and would prefer to switch to plan B.
* The calls duration is longer in October/ November. Seems reasonable: when it is cold outside people prefer to stay home and speak on the phone.

### Step 4. Business Metrics Analysis <a name="step4"></a>

* We are going to define non-active users: the one's that have not been using our service for month.
* 1 Month seems to bee rather logical bound: less then a month could be explained by a long trip abroad/ but more than a month means a user has left.

In [84]:
#data grouped by user_id and last month of usage 
grouped_for_churn = telecom_merged.groupby('user_id').agg(
    {'operator_id':'nunique','call_duration':'sum','total_call_duration'
                                             :'sum','tariff_plan':'first','event_month':'max'}).reset_index()
grouped_for_churn.rename(columns={'event_month':'last_month'}, inplace = True)
grouped_for_churn

user_id  operator_id  call_duration  total_call_duration tariff_plan  \
0     166377            5         317987               388221           B   
1     166391            2            260                  929           C   
2     166392            3          16652                20382           C   
3     166399            1            244                  789           C   
4     166405           10        1147728              1447230           B   
..       ...          ...            ...                  ...         ...   
302   168583            2            919                 1759           B   
303   168598            1           4186                 4871           C   
304   168601            2          32676                42871           C   
305   168603            1            905                 1217           B   
306   168606            1           5101                 5612           C   

     last_month  
0            11  
1            11  
2            11  
3            10  
4            11  
..          ...  
302          11  
303          11  
304          11  
305          11  
306          11  

[307 rows x 6 columns]

In [85]:
def churn(row):
    ### if user last used our service more than moth ago(the last month is november=11, then we assign him to left
    last_month = row['last_month']
    if last_month < 11:
        left = 1
    else:
        left = 0
    return left
grouped_for_churn['churn'] = grouped_for_churn.apply(churn,axis=1)
grouped_for_churn

user_id  operator_id  call_duration  total_call_duration tariff_plan  \
0     166377            5         317987               388221           B   
1     166391            2            260                  929           C   
2     166392            3          16652                20382           C   
3     166399            1            244                  789           C   
4     166405           10        1147728              1447230           B   
..       ...          ...            ...                  ...         ...   
302   168583            2            919                 1759           B   
303   168598            1           4186                 4871           C   
304   168601            2          32676                42871           C   
305   168603            1            905                 1217           B   
306   168606            1           5101                 5612           C   

     last_month  churn  
0            11      0  
1            11      0  
2            11      0  
3            10      1  
4            11      0  
..          ...    ...  
302          11      0  
303          11      0  
304          11      0  
305          11      0  
306          11      0  

[307 rows x 7 columns]

In [86]:
# plot stay/left by plan
barplot = grouped_for_churn.groupby('churn').agg({'user_id':'count'}).reset_index()
fig = px.bar(barplot,x='churn',y='user_id',color="churn",
            labels={'user_id':'Number of Users','churn':'Churn'})
fig.update_layout(title_text='Number of Users who Stayed/ Left')
fig.show()


In [87]:
#total churn rate
print(round((grouped_for_churn.query('churn =="1"')['user_id'].nunique() / grouped_for_churn['user_id'].nunique()) * 100),'%')

15 %



* The churn rate is 15%. 

+ Now we are going to group the users by user_id and internal/external calls.
+ Then calculate the total amount of months the user is staying with us.


All these columns will help us calculate plan revenue for each user.


In [88]:
#data grouped by user_id and internal/external calls in order to calculate revenue 
grouped_final = telecom_merged.groupby(['user_id','internal']).agg({'date':'max','date_start':'first'
    ,'call_duration':'sum','tariff_plan':'first'}).reset_index()
grouped_final['total_months'] = grouped_final['date'].sub(grouped_final['date_start'],
                                                          axis=0) / np.timedelta64(1, 'M')
# a column for call duration per month
grouped_final['call_duration_per_month'] = grouped_final['call_duration'] / grouped_final['total_months']
grouped_final

user_id  internal       date date_start  call_duration tariff_plan  \
0     166377     False 2019-11-28 2019-08-01         317855           B   
1     166377      True 2019-11-27 2019-08-01            132           B   
2     166391     False 2019-11-22 2019-08-01            249           C   
3     166391      True 2019-08-16 2019-08-01             11           C   
4     166392     False 2019-11-28 2019-08-01          16652           C   
..       ...       ...        ...        ...            ...         ...   
481   168601     False 2019-11-28 2019-10-31          32676           C   
482   168601      True 2019-11-12 2019-10-31              0           C   
483   168603     False 2019-11-28 2019-10-31            905           B   
484   168606     False 2019-11-19 2019-10-31           1492           C   
485   168606      True 2019-11-15 2019-10-31           3609           C   

     total_months  call_duration_per_month  
0        3.909731             81298.427757  
1        3.876876                34.048030  
2        3.712602                67.068866  
3        0.492823                22.320375  
4        3.909731              4259.116324  
..            ...                      ...  
481      0.919937             35519.833125  
482      0.394259                 0.000000  
483      0.919937               983.763281  
484      0.624243              2390.095658  
485      0.492823              7323.112125  

[486 rows x 8 columns]

* We will check wether there are users who use more than 2000 free minutes on internal calls (per month)

In [89]:
#2000minutes = 2000*60 =120000seconds
grouped_final.query('call_duration_per_month>120000 & internal==True')

Empty DataFrame
Columns: [user_id, internal, date, date_start, call_duration, tariff_plan, total_months, call_duration_per_month]
Index: []

* Apparently, there are no such users.

In [90]:
#a function that calculates the revenue per month per user for plan B (without adding plan cost)
def if_b(row):
    internal = row['internal']
    duration = row['call_duration_per_month']
    #the users are paying extra only for external calls
    if internal==False:
            paying_b = 0.5 * duration/60

    else:
        paying_b = 0
        
    return round(paying_b)
grouped_final['B_revenue_per_month']  =  grouped_final.apply(if_b,axis=1)
grouped_final

user_id  internal       date date_start  call_duration tariff_plan  \
0     166377     False 2019-11-28 2019-08-01         317855           B   
1     166377      True 2019-11-27 2019-08-01            132           B   
2     166391     False 2019-11-22 2019-08-01            249           C   
3     166391      True 2019-08-16 2019-08-01             11           C   
4     166392     False 2019-11-28 2019-08-01          16652           C   
..       ...       ...        ...        ...            ...         ...   
481   168601     False 2019-11-28 2019-10-31          32676           C   
482   168601      True 2019-11-12 2019-10-31              0           C   
483   168603     False 2019-11-28 2019-10-31            905           B   
484   168606     False 2019-11-19 2019-10-31           1492           C   
485   168606      True 2019-11-15 2019-10-31           3609           C   

     total_months  call_duration_per_month  B_revenue_per_month  
0        3.909731             81298.427757                  677  
1        3.876876                34.048030                    0  
2        3.712602                67.068866                    1  
3        0.492823                22.320375                    0  
4        3.909731              4259.116324                   35  
..            ...                      ...                  ...  
481      0.919937             35519.833125                  296  
482      0.394259                 0.000000                    0  
483      0.919937               983.763281                    8  
484      0.624243              2390.095658                   20  
485      0.492823              7323.112125                    0  

[486 rows x 9 columns]

In [91]:
#a function that calculates the revenue per user per month for plan C (without adding plan cost)
def if_c(row):
    internal = row['internal']
    duration = row['call_duration_per_month']
    #the users are paying extra only for external calls
    if internal==False:
            paying_c = 0.7 * duration/60

    else:
        paying_c = 0
        
    return round(paying_c)
grouped_final['C_revenue_per_month']  =  grouped_final.apply(if_c,axis=1)
grouped_final

user_id  internal       date date_start  call_duration tariff_plan  \
0     166377     False 2019-11-28 2019-08-01         317855           B   
1     166377      True 2019-11-27 2019-08-01            132           B   
2     166391     False 2019-11-22 2019-08-01            249           C   
3     166391      True 2019-08-16 2019-08-01             11           C   
4     166392     False 2019-11-28 2019-08-01          16652           C   
..       ...       ...        ...        ...            ...         ...   
481   168601     False 2019-11-28 2019-10-31          32676           C   
482   168601      True 2019-11-12 2019-10-31              0           C   
483   168603     False 2019-11-28 2019-10-31            905           B   
484   168606     False 2019-11-19 2019-10-31           1492           C   
485   168606      True 2019-11-15 2019-10-31           3609           C   

     total_months  call_duration_per_month  B_revenue_per_month  \
0        3.909731             81298.427757                  677   
1        3.876876                34.048030                    0   
2        3.712602                67.068866                    1   
3        0.492823                22.320375                    0   
4        3.909731              4259.116324                   35   
..            ...                      ...                  ...   
481      0.919937             35519.833125                  296   
482      0.394259                 0.000000                    0   
483      0.919937               983.763281                    8   
484      0.624243              2390.095658                   20   
485      0.492823              7323.112125                    0   

     C_revenue_per_month  
0                    948  
1                      0  
2                      1  
3                      0  
4                     50  
..                   ...  
481                  414  
482                    0  
483                   11  
484                   28  
485                    0  

[486 rows x 10 columns]

In [92]:
#a function that calculates the revenue per user for plan A (without adding plan cost)
def if_a(row):
    internal = row['internal']
    duration = row['call_duration_per_month']
    #the users are paying extra only for external calls
    if internal==False:
            paying_a = 0.7 * duration/60

    else:
        paying_a = 0
        
    return round(paying_a)
grouped_final['A_revenue_per_month']  =  grouped_final.apply(if_a,axis=1)
grouped_final

user_id  internal       date date_start  call_duration tariff_plan  \
0     166377     False 2019-11-28 2019-08-01         317855           B   
1     166377      True 2019-11-27 2019-08-01            132           B   
2     166391     False 2019-11-22 2019-08-01            249           C   
3     166391      True 2019-08-16 2019-08-01             11           C   
4     166392     False 2019-11-28 2019-08-01          16652           C   
..       ...       ...        ...        ...            ...         ...   
481   168601     False 2019-11-28 2019-10-31          32676           C   
482   168601      True 2019-11-12 2019-10-31              0           C   
483   168603     False 2019-11-28 2019-10-31            905           B   
484   168606     False 2019-11-19 2019-10-31           1492           C   
485   168606      True 2019-11-15 2019-10-31           3609           C   

     total_months  call_duration_per_month  B_revenue_per_month  \
0        3.909731             81298.427757                  677   
1        3.876876                34.048030                    0   
2        3.712602                67.068866                    1   
3        0.492823                22.320375                    0   
4        3.909731              4259.116324                   35   
..            ...                      ...                  ...   
481      0.919937             35519.833125                  296   
482      0.394259                 0.000000                    0   
483      0.919937               983.763281                    8   
484      0.624243              2390.095658                   20   
485      0.492823              7323.112125                    0   

     C_revenue_per_month  A_revenue_per_month  
0                    948                  948  
1                      0                    0  
2                      1                    1  
3                      0                    0  
4                     50                   50  
..                   ...                  ...  
481                  414                  414  
482                    0                    0  
483                   11                   11  
484                   28                   28  
485                    0                    0  

[486 rows x 11 columns]

* Now we will group the data by user_id ( combining internal and external calls).
* Then add to each revenue per month a tariff plan cost.
* This will provide us with total monthly revenue for each user and each plan.

In [93]:
grouped_final = grouped_final.groupby('user_id').agg({'tariff_plan':'first','total_months':'max',
                                                      'B_revenue_per_month':'sum','C_revenue_per_month':
                                       'sum','A_revenue_per_month':'sum'}).reset_index()
## adding plan cost for each user 
grouped_final['B_revenue_per_month'] = round(grouped_final['B_revenue_per_month'] + 2000)
grouped_final['C_revenue_per_month'] = round(grouped_final['C_revenue_per_month'] + 1000)
grouped_final['A_revenue_per_month'] = round(grouped_final['A_revenue_per_month'] + 5000)
grouped_final

user_id tariff_plan  total_months  B_revenue_per_month  \
0     166377           B      3.909731                 2677   
1     166391           C      3.712602                 2001   
2     166392           C      3.909731                 2035   
3     166399           C      2.726955                 2001   
4     166405           B      3.876876                 4466   
..       ...         ...           ...                  ...   
302   168583           B      0.919937                 2008   
303   168598           C      0.919937                 2038   
304   168601           C      0.919937                 2296   
305   168603           B      0.919937                 2008   
306   168606           C      0.624243                 2020   

     C_revenue_per_month  A_revenue_per_month  
0                   1948                 5948  
1                   1001                 5001  
2                   1050                 5050  
3                   1001                 5001  
4                   4453                 8453  
..                   ...                  ...  
302                 1012                 5012  
303                 1053                 5053  
304                 1414                 5414  
305                 1011                 5011  
306                 1028                 5028  

[307 rows x 6 columns]

* Now we can define an optimal plan for each user, overpaying users and possible loss

In [94]:
grouped_final.query('A_revenue_per_month < C_revenue_per_month & A_revenue_per_month < B_revenue_per_month')

Empty DataFrame
Columns: [user_id, tariff_plan, total_months, B_revenue_per_month, C_revenue_per_month, A_revenue_per_month]
Index: []

There are no users that would prefer A plan over C and B.

In [95]:
#defining optimal plan
def optimal(row):
    #only plans B or C could be optimal 
    if_b = row['B_revenue_per_month']
    if_c = row['C_revenue_per_month']
    if  if_b < if_c:
        optimal = 'B'
    else:
        optimal  = 'C'
            
    return optimal
grouped_final['optimal_plan']  =  grouped_final.apply(optimal,axis=1)
    
grouped_final

user_id tariff_plan  total_months  B_revenue_per_month  \
0     166377           B      3.909731                 2677   
1     166391           C      3.712602                 2001   
2     166392           C      3.909731                 2035   
3     166399           C      2.726955                 2001   
4     166405           B      3.876876                 4466   
..       ...         ...           ...                  ...   
302   168583           B      0.919937                 2008   
303   168598           C      0.919937                 2038   
304   168601           C      0.919937                 2296   
305   168603           B      0.919937                 2008   
306   168606           C      0.624243                 2020   

     C_revenue_per_month  A_revenue_per_month optimal_plan  
0                   1948                 5948            C  
1                   1001                 5001            C  
2                   1050                 5050            C  
3                   1001                 5001            C  
4                   4453                 8453            C  
..                   ...                  ...          ...  
302                 1012                 5012            C  
303                 1053                 5053            C  
304                 1414                 5414            C  
305                 1011                 5011            C  
306                 1028                 5028            C  

[307 rows x 7 columns]

In [96]:
#defining overpaying users
def overpaying(row):
    current=row['tariff_plan']
    optimal = row['optimal_plan']
    if optimal != current:
        overpaying=1
    else:
        overpaying=0
    return overpaying
grouped_final['overpaying']  =  grouped_final.apply(overpaying,axis=1)
    
grouped_final

user_id tariff_plan  total_months  B_revenue_per_month  \
0     166377           B      3.909731                 2677   
1     166391           C      3.712602                 2001   
2     166392           C      3.909731                 2035   
3     166399           C      2.726955                 2001   
4     166405           B      3.876876                 4466   
..       ...         ...           ...                  ...   
302   168583           B      0.919937                 2008   
303   168598           C      0.919937                 2038   
304   168601           C      0.919937                 2296   
305   168603           B      0.919937                 2008   
306   168606           C      0.624243                 2020   

     C_revenue_per_month  A_revenue_per_month optimal_plan  overpaying  
0                   1948                 5948            C           1  
1                   1001                 5001            C           0  
2                   1050                 5050            C           0  
3                   1001                 5001            C           0  
4                   4453                 8453            C           1  
..                   ...                  ...          ...         ...  
302                 1012                 5012            C           1  
303                 1053                 5053            C           0  
304                 1414                 5414            C           0  
305                 1011                 5011            C           1  
306                 1028                 5028            C           0  

[307 rows x 8 columns]

In [98]:
##calculating possible loss
def loss(row):
#if user is not using his optimal plan, 
#then the possible loss is the difference in revenue between currrent and optimal plans 
    optimal=row['optimal_plan']
    current = row['tariff_plan']
    if_b = row['B_revenue_per_month']
    if_c = row['C_revenue_per_month']
    if_a = row['A_revenue_per_month']
    if current == 'C':
        if optimal =="B":
            loss = if_c - if_b
        else:
            loss = 0
    elif current == 'B':
        if optimal == 'C':
            loss = if_b - if_c
        else:
            loss = 0
    else:
        if optimal == 'C':
            loss = if_a - if_c
        else:
            loss = if_a - if_b
    return round(loss)
grouped_final['loss']  =  grouped_final.apply(loss,axis=1)
    
grouped_final.query('tariff_plan =="A"')

user_id tariff_plan  total_months  B_revenue_per_month  \
6     166407           A      3.876876                 2062   
8     166481           A      2.201277                 2000   
19    166541           A      3.712602                 2402   
22    166582           A      3.646892                20907   
26    166609           A      3.088359                 2023   
44    166713           A      3.416908                 2023   
46    166725           A      3.416908                 2265   
60    166843           A      3.252634                 2064   
62    166879           A      3.219779                 2086   
64    166896           A      3.154069                 2056   
66    166901           A      3.186924                 2125   
68    166916           A      3.186924                 3007   
117   167158           A      2.792665                 2036   
124   167185           A      2.759810                 2162   
137   167265           A      2.595536                 2000   
141   167285           A      1.412760                 3524   
161   167497           A      2.332697                 2654   
175   167626           A      0.854227                32707   
177   167631           A      0.459968                 2000   
178   167634           A      1.905583                 2158   
199   167799           A      1.905583                 2519   
204   167828           A      1.872728                 2795   
220   167949           A      1.708454                 2375   
246   168048           A      1.609889                 2001   
248   168062           A      1.577034                 5057   
258   168121           A      1.478470                 2174   
259   168128           A      1.379905                 2012   
264   168187           A      1.412760                 8510   
266   168193           A      1.412760                 2032   
271   168252           A      1.379905                10927   
272   168253           A      1.347050                 4826   
277   168295           A      1.248486                 2134   
284   168361           A      1.182776                31877   
290   168459           A      1.051356                 2000   

     C_revenue_per_month  A_revenue_per_month optimal_plan  overpaying   loss  
6                   1087                 5087            C           1   4000  
8                   1000                 5000            C           1   4000  
19                  1562                 5562            C           1   4000  
22                 27470                31470            B           1  10563  
26                  1032                 5032            C           1   4000  
44                  1033                 5033            C           1   4000  
46                  1370                 5370            C           1   4000  
60                  1089                 5089            C           1   4000  
62                  1121                 5121            C           1   4000  
64                  1079                 5079            C           1   4000  
66                  1176                 5176            C           1   4000  
68                  2409                 6409            C           1   4000  
117                 1051                 5051            C           1   4000  
124                 1227                 5227            C           1   4000  
137                 1000                 5000            C           1   4000  
141                 3134                 7134            C           1   4000  
161                 1916                 5916            C           1   4000  
175                43990                47990            B           1  15283  
177                 1000                 5000            C           1   4000  
178                 1221                 5221            C           1   4000  
199                 1727                 5727            C           1   4000  
204                 2113               

* We will add churn column to our dataset.

In [99]:
#merging churn and overpaying

final_telecom = grouped_final.merge(grouped_for_churn[['user_id','churn']],on='user_id',how='left')
final_telecom

user_id tariff_plan  total_months  B_revenue_per_month  \
0     166377           B      3.909731                 2677   
1     166391           C      3.712602                 2001   
2     166392           C      3.909731                 2035   
3     166399           C      2.726955                 2001   
4     166405           B      3.876876                 4466   
..       ...         ...           ...                  ...   
302   168583           B      0.919937                 2008   
303   168598           C      0.919937                 2038   
304   168601           C      0.919937                 2296   
305   168603           B      0.919937                 2008   
306   168606           C      0.624243                 2020   

     C_revenue_per_month  A_revenue_per_month optimal_plan  overpaying  loss  \
0                   1948                 5948            C           1   729   
1                   1001                 5001            C           0     0   
2                   1050                 5050            C           0     0   
3                   1001                 5001            C           0     0   
4                   4453                 8453            C           1    13   
..                   ...                  ...          ...         ...   ...   
302                 1012                 5012            C           1   996   
303                 1053                 5053            C           0     0   
304                 1414                 5414            C           0     0   
305                 1011                 5011            C           1   997   
306                 1028                 5028            C           0     0   

     churn  
0        0  
1        0  
2        0  
3        1  
4        0  
..     ...  
302      0  
303      0  
304      0  
305      0  
306      0  

[307 rows x 10 columns]

* We will calculate he share of overpaying users per plan.
* And the churn rate per plan.

In [100]:
#data grouped by plan with churn rate calculated 
plan = final_telecom.groupby('tariff_plan').agg({'user_id':'count','churn':'sum','overpaying':'sum'}).reset_index()
plan['churn_rate'] = plan['churn'] / plan['user_id']
plan

tariff_plan  user_id  churn  overpaying  churn_rate
0           A       34      4          34    0.117647
1           B      112     16         110    0.142857
2           C      161     26           3    0.161491

In [101]:
#share of overpaying users per plan
plan['overpaying_share'] = plan['overpaying'] / plan['user_id']
plan

tariff_plan  user_id  churn  overpaying  churn_rate  overpaying_share
0           A       34      4          34    0.117647          1.000000
1           B      112     16         110    0.142857          0.982143
2           C      161     26           3    0.161491          0.018634

In [102]:
#churn visualisation
fig = px.bar(plan,x='tariff_plan',y='churn_rate',color="tariff_plan",
            labels={'churn_rate':'Churn Rate','churn':'Churn','tariff_plan':'Plan'})
fig.update_layout(title_text='Churn Rate By Plan')
fig.show()

In [103]:
#share of overpaying visualisation
fig = px.bar(plan,x='tariff_plan',y='overpaying_share',color="tariff_plan",
            labels={'overpaying_share':'The Share of Overpaying Clients','tariff_plan':'Plan'})
fig.update_layout(title_text='The Share of Overpaying Clients By Plan')
fig.show()

* Churn rate is the highest for C plan.
* The biggest share of overpaying users is for plan A.

* We can calculate how many users are overpaying.

In [104]:
#number of active overpaying users
final_telecom.query('overpaying =="1" & churn =="0"')['user_id'].nunique()

126

* We will now calculate possible total loss per month and loss per user.

In [105]:
#total loss per month
final_telecom['loss'].sum()

269805

In [106]:
#loss per month per user
round(final_telecom['loss'].sum() / final_telecom['user_id'].nunique())

879

### Conclusions
* We have created a column that indicates on users that are overpaying.
* We have now 126 active users who are overpaying and may be offered to switch.
* If they do switch plans, our maximum possible loss per user will be 879 dollars per month. 


### Step 5. Hypothesis testing <a name="step5"></a>

* Now we are going to check the following hypothesis:
    * Ho= The difference in churn rate between overpaying and not overpaying users is statistically insignificant(the proportion of users who leave does not differ between two groups)
    * H1 = The difference in churn rate between overpaying and not overpaying users is statistically significant(the proportion of users who leave does differ between groups)

* First lets check to size of our samples

In [107]:
#samples for hypothesis testing 
final_telecom.query('overpaying ==1')['user_id'].nunique()

147

In [108]:
final_telecom.query('overpaying ==0')['user_id'].nunique()

160

* The samples are almost balanced. 
* We will now perform a z-test.

In [109]:
#hypothesis_test
alpha=0.05
    #churn for each group
churn1 = final_telecom.query('churn == 1 & overpaying == 0')['user_id'].nunique()
churn2 = final_telecom.query('churn == 1 & overpaying == 1')['user_id'].nunique()
    
    #trials for each group
total1 = final_telecom.query('overpaying == 0')['user_id'].nunique()
total2 = final_telecom.query('overpaying == 1')['user_id'].nunique()
    
    #proportion of successes in each group
p1 = churn1 / total1
p2 = churn2 / total2
    
    #combined proportion
p_combined = (churn1 + churn2) / (total1 + total2)

    #difference
difference = p1 - p2
    
z_value = difference / math.sqrt(p_combined * (1 - p_combined) * (1/total1 + 1/total2))
    
distr = stats.norm(0,1)
    
p_value = (1 - distr.cdf(abs(z_value))) * 2
    
print('p_value:', p_value)
    
if (p_value < alpha):
    print('Reject H0 for churn rates for not overpaying and overpaying clients')
else:
    print('Fail to reject H0 for churn rates for not overpaying and overpaying clients')
    

p_value: 0.7425756472428942
Fail to reject H0 for churn rates for not overpaying and overpaying clients


* The test shows that there is no statistically significant difference between groups, which implies that overpaying users do not leave more often than others.


#### Conclusions
* We have **126 active users who are overpaying** for their current contract.
* If we offer than to switch the plan the  **maximum possible loss will be 879 dollars per month per user.**
* There is no statistically signifficant difference between overpaying and not overpaying users as for the churn rate.



#### Recommendations
* Perhaps, it would be smart to run an A/B test before offering the campaing to all overpaying users.
* The question is how to measure the increase in loyalty? It is possible to conduct an interview/ online questionnaire and check the change in users behaviour after the offer.
* The Sales Departmnet then should cosider what overweighs: possible loss or increase in loyalty.
